<div style="text-align: center; font-family: 'charter bt pro roman'; color: rgb(0, 65, 75);">
    <h1>
    GDP Vintages, Releases and Revisions datasets
    </h1>
</div>

<div style="text-align: center; font-family: 'charter bt pro roman'; color: rgb(0, 65, 75);">
<h3>
Documentation
<br>
____________________
<br>
</h3>
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    This 
    <span style="color: rgb(0, 65, 75);">jupyter notebook</span>
    provides a step-by-step guide to <b>data building</b> regarding the project <b>'Revisiones y sesgos en las estimaciones preliminares del PBI en el Perú'</b>. This guide covers the creation of GDP mid-term revision dataset for each sector. A key step is the construction at par of what we will call “The ‘t+h’ structure”. This dataset is similar to that of the GDP growth vintages by sector, but instead of growth rate values, it contains values of type “t+h”, where h indicates how many months have passed since the preliminary growth rate was first published; that is, this jupyter notebook also covers the creation of vintages datasets of growth rates associated with a horizon (<b>h</b>).
</div>

<div style="text-align: center; font-family: 'PT Serif Pro Book'; color: rgb(0, 65, 75); font-size: 16px;">
    Jason Cruz
    <br>
    <a href="mailto:jj.cruza@up.edu.pe" style="color: rgb(0, 153, 123); font-size: 16px;">
        jj.cruza@up.edu.pe
    </a>
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;line-height: 1.5;">
<span style="font-size: 34px;">&#128452;</span> The 't+h' structure should be available for all sectors and frequencies.
    <br>
    <span style="font-size: 24px;">&#8987;</span> Available since <b>1994-2024</b> (Table 1) and since <b>1997-2024</b> (Table 2). 
    <br>
</div>

<div style="font-family: Amaya; text-align: left; color: rgb(0, 65, 75); font-size:16px">The following <b>outline is functional</b>. By utilising the provided buttons, users are able to enhance their experience by browsing this script.<div/>

<div id="outilne">
   <!-- Contenido de la celda de destino -->
</div>

<div style="background-color: #292929; padding: 10px; line-height: 1.5; font-family: 'PT Serif Pro Book';">
    <h2 style="text-align: left; color: #E0E0E0;">
        Outline
    </h2>
    <br>
    <a href="#libraries" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        Libraries</a>
    <br>
    <a href="#setup" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        Initial set-up</a>
    <br>
    <a href="#1" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        1. Economic sector selector</a>
    <br>
    <a href="#2" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        2. Create horizon datasets</a>
    <br>
    <a href="#2.1." style="color: #94FFD8; font-size: 16px; margin-left: 20px;">
        2.1. Loading growth rate datasets from postgresql.</a>
    <br>
    <a href="#2.2." style="color: #94FFD8; font-size: 16px; margin-left: 20px;">
        2.2. Creating horizon dataset step by step.</a> 
    <br>
    <a href="#3" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        3. Create growth rates by horizon dataset</a>
    <br>
    <a href="#4" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        4. Create vintages and releases datasets</a>
    <br>
    <a href="#5" style="color: #E0E0E0; font-size: 18px; margin-left: 0px;">
        5. Loading to SQL</a>
    <br>
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    Any questions or issues regarding the coding, please email Jason Cruz <a href="mailto:jj.cruza@alum.up.edu.pe" style="color: rgb(0, 153, 123); text-decoration: none;"><span style="font-size: 24px;">&#x2709;</span>
    </a>.
    <div/>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    If you don't have the libraries below, please use the following code (as example) to install the required libraries.
    <div/>

In [ ]:
#!pip install os # Comment this code with "#" if you have already installed this library.

<div id="libraries">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark;">
    <h2>
    Libraries
    </h2>
    <div/>

In [2]:
# POSTGRESSQL
import os
from sqlalchemy import create_engine

# HORIZON DATASETS
import pandas as pd
import numpy as np
import re


<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">Back to the outline.</a>
</div>

<div id="setup">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark;">
    <h2>
    Initial set-up
    </h2>
    <div/>

<p style="font-family: PT Serif Pro Book; text-align: left; color:dark; font-size:16px"> The following function will establish a connection to the <code>gdp_revisions_datasets</code> database in <code>PostgreSQL</code>. The <b>input data</b> used in this jupyter notebook will be loaded from this <code>PostgreSQL</code> database, and similarly, all <b>output data</b> generated by this jupyter notebook will be stored in that database. Ensure that you set the necessary parameters to access the server once you have obtained the required permissions.<p/>
    
<p style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
To request permissions, please email Jason Cruz <a href="mailto:jj.cruza@alum.up.edu.pe" style="color: rgb(0, 153, 123); text-decoration: none;"> <span style="font-size: 24px;">&#x2709;</span>
    </a>.
<p/>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    <span style="font-size: 24px; color: #FFA823; font-weight: bold;">&#9888;</span>
    Enter your user credentials to acces to SQL.
    <div/>

In [3]:
def create_sqlalchemy_engine():
    """
    Function to create an SQLAlchemy engine using environment variables.
    
    Returns:
        engine: SQLAlchemy engine object.
    """
    # Get environment variables
    user = os.environ.get('CIUP_SQL_USER')  # Get the SQL user from environment variables
    password = os.environ.get('CIUP_SQL_PASS')  # Get the SQL password from environment variables
    host = os.environ.get('CIUP_SQL_HOST')  # Get the SQL host from environment variables
    port = 5432  # Set the SQL port to 5432
    database = 'gdp_revisions_datasets'  # Set the database name 'gdp_revisions_datasets' from SQL

    # Check if all environment variables are defined
    if not all([host, user, password]):
        raise ValueError("Some environment variables are missing (CIUP_SQL_HOST, CIUP_SQL_USER, CIUP_SQL_PASS)")

    # Create connection string
    connection_string = f"postgresql://{user}:{password}@{host}:{port}/{database}"

    # Create SQLAlchemy engine
    engine = create_engine(connection_string)
    
    return engine

<div style="text-align: left;">
    <span style="font-size: 24px; color: rgb(255, 32, 78); font-weight: bold;">&#9888;</span>
    <span style="font-family: PT Serif Pro Book; color: black; font-size: 16px;">
        Import all other functions required by this jupyter notebook.
    </span>
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color:dark; font-size:16px"> Please, check the script <code>gdp_revisions_datasets_functions.py</code> which contains all the functions required by this jupyter notebook. The functions there are ordered according to the <a href="#outilne" style="color: #3d30a2;">sections</a> of this jupyter notebok.<div/>

In [4]:
from gdp_revisions_datasets_functions import *

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">Back to the outline.</a>
</div>

<div id="1">
   <!-- Contenido de la celda de destino -->
</div>

<h1><span style = "color: rgb(0, 65, 75); font-family: PT Serif Pro Book; color: dark;">1.</span> <span style = "color: dark; font-family: PT Serif Pro Book;">Economic sector and data frequency selector</span></h1>

<div id="steps-1">
   <!-- Contenido de la celda de destino -->
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <a href="#step-1-1" style="text-decoration: none; color: #006769"> <span style="font-size: 24px; color: rgb(0, 65, 75);">&#10122;</span> Select economic sector</a>
    <br>
    <a href="#step-1-2" style="text-decoration: none; color: #006769"><span style="font-size: 24px; color: rgb(0, 65, 75)">&#10123;</span> Select frequency</a>
</div>

<div id="step-1-1">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10122;</span> <span>Select economic sector</span>
  </div>

In [5]:
# Call the function to show the popup window
sector = show_option_window()
print("Selected economic sector:", sector)

Selected economic sector: gdp


<div id="step-1-2">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10123;</span> <span>Select frequency</span>
  </div>

In [5]:
# Call the function to show the popup window
frequency = show_frequency_window()
print("Selected frequency:", frequency)

Selected frequency: monthly


<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 20px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#steps-1" style="color: #006769; text-decoration: none;">⮝</a>
    </span> 
    <a href="#steps-1" style="color: #006769; text-decoration: none;">Back to steps.</a>
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">Back to the outline.</a>
</div>

<div id="2">
   <!-- Contenido de la celda de destino -->
</div>

<h1><span style = "color: rgb(0, 65, 75); font-family: PT Serif Pro Book; color: dark;">2.</span> <span style = "color: dark; font-family: PT Serif Pro Book;">Create horizon datasets</span></h1>

<div id="2.1.">
   <!-- Contenido de la celda de destino -->
</div>

<h2><span style = "color: rgb(0, 65, 75); font-family: PT Serif Pro Book;">2.1. </span> <span style = "color: dark; font-family: PT Serif Pro Book;">Loading growth rate datasets from <code>PostgresSQL</code></span></h2>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    Connect to SQL.
    <div/>

In [6]:
# Connect to SQL
engine = create_sqlalchemy_engine()

# SQL Query
query = f"SELECT * FROM {sector}_{frequency}_growth_rates;" # Please change your query to PosgtresSQL as you see fit

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    Comment the code below if you want the default option (display rows and columns of the dataframe in a limited way)
    <div/>

In [7]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    Check the loaded dataframe.
    <div/>

In [8]:
# Read growth rates dataset as DataFrame
globals()[f'{sector}_{frequency}_growth_rates'] = pd.read_sql(query, engine)
growth_rates = globals()[f'{sector}_{frequency}_growth_rates']
growth_rates_df = growth_rates.copy()
growth_rates_df.head(150)

year id_ns       date  sep_2011  oct_2011  nov_2011  dic_2011  ene_2012  \
0    2013    01 2013-01-04       5.9       5.3       5.1       6.0       5.5   
1    2013    02 2013-01-11       5.9       5.3       5.1       6.0       5.5   
2    2013    03 2013-01-18       NaN       NaN       5.1       6.0       5.5   
3    2013    04 2013-01-25       NaN       NaN       5.1       6.0       5.5   
4    2013    05 2013-02-01       NaN       NaN       5.1       6.0       5.5   
5    2013    06 2013-02-08       NaN       NaN       5.1       6.0       5.5   
6    2013    07 2013-02-15       NaN       NaN       5.1       6.0       5.5   
7    2013    08 2013-02-22       NaN       NaN       NaN       6.0       5.5   
8    2013    09 2013-03-01       NaN       NaN       NaN       6.0       5.5   
9    2013    10 2013-03-08       NaN       NaN       NaN       6.0       5.5   
10   2013    11 2013-03-15       NaN       NaN       NaN       6.0       5.5   
11   2013    12 2013-03-22       NaN       NaN       NaN       NaN       5.5   
12   2013    13 2013-04-05       NaN       NaN       NaN       NaN       5.5   
13   2013    14 2013-04-12       NaN       NaN       NaN       NaN       5.5   
14   2013    15 2013-04-19       NaN       NaN       NaN       NaN       NaN   
15   2013    16 2013-04-26       NaN       NaN       NaN       NaN       NaN   
16   2013    17 2013-05-03       NaN       NaN       NaN       NaN       NaN   
17   2013    18 2013-05-10       NaN       NaN       NaN       NaN       NaN   
18   2013    19 2013-05-17       NaN       NaN       NaN       NaN       NaN   
19   2013    20 2013-05-24       NaN       NaN       NaN       NaN       NaN   
20   2013    21 2013-05-31       NaN       NaN       NaN       NaN       NaN   
21   2013    22 2013-06-07       NaN       NaN       NaN       NaN       NaN   
22   2013    23 2013-06-14       NaN       NaN       NaN       NaN       NaN   
23   2013    24 2013-06-21       NaN       NaN       NaN       NaN       NaN   
24   2013    25 2013-06-27       NaN       NaN       NaN       NaN       NaN   
25   2013    26 2013-07-05       NaN       NaN       NaN       NaN       NaN   
26   2013    27 2013-07-12       NaN       NaN       NaN       NaN       NaN   
27   2013    28 2013-07-19       NaN       NaN       NaN       NaN       NaN   
28   2013    29 2013-07-26       NaN       NaN       NaN       NaN       NaN   
29   2013    30 2013-08-09       NaN       NaN       NaN       NaN       NaN   
30   2013    31 2013-08-16       NaN       NaN       NaN       NaN       NaN   
31   2013    32 2013-08-23       NaN       NaN       NaN       NaN       NaN   
32   2013    33 2013-08-29       NaN       NaN       NaN       NaN       NaN   
33   2013    34 2013-09-06       NaN       NaN       NaN       NaN       NaN   
34   2013    35 2013-09-13       NaN       NaN       NaN       NaN       NaN   
35   2013    36 2013-09-20       NaN       NaN       NaN       NaN       NaN   
36   2013    37 2013-09-27       NaN       NaN       NaN       NaN       NaN   
37   2013    38 2013-10-04       NaN       NaN       NaN       NaN       NaN   
38   2013    39 2013-10-11       NaN       NaN       NaN       NaN       NaN   
39   2013    40 2013-10-18       NaN       NaN       NaN       NaN       NaN   
40   2013    41 2013-10-25       NaN       NaN       NaN       NaN       NaN   
41   2013    42 2013-10-31       NaN       NaN       NaN       NaN       NaN   
42   2013    43 2013-11-08       NaN       NaN       NaN       NaN       NaN   
43   2013    44 2013-11-15       NaN       NaN       NaN       NaN       NaN   
44   2013    45 2013-11-22       NaN       NaN       NaN       NaN       NaN   
45   2013    46 2013-11-29       NaN       NaN       NaN       NaN       NaN   
46   2013    47 2013-12-06       NaN       NaN       NaN       NaN       NaN   
47   2013    48 2013-12-13       NaN       NaN       NaN       NaN       NaN   
48   2013    49 2013-12-20       NaN       NaN       NaN       NaN       NaN   
49   

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">Back to the outline.</a>
</div>

<div id="2.2.">
   <!-- Contenido de la celda de destino -->
</div>

<div id="2.3.">
   <!-- Contenido de la celda de destino -->
</div>

<h2><span style = "color: rgb(0, 65, 75); font-family: PT Serif Pro Book;">2.2.</span>
    <span style = "color: dark; font-family: PT Serif Pro Book;">
    Creating horizon dataset step by step
    </span>
    </h2>

<div id="steps-2">
   <!-- Contenido de la celda de destino -->
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <a href="#step-2-1" style="text-decoration: none; color: #006769"> <span style="font-size: 24px; color: rgb(0, 65, 75);">&#10122;</span> Replace decimal values by “t+h” values only in the rows representing a new rung</a>
    <br>
    <a href="#step-2-2" style="text-decoration: none; color: #006769"><span style="font-size: 24px; color: rgb(0, 65, 75)">&#10123;</span> Concatenate first 3 columns: year, date, id_ns </a>
    <br>
    <a href="#step-2-3" style="text-decoration: none; color: #006769"><span style="font-size: 24px; color: rgb(0, 65, 75)">&#10124;</span> Convert columns to string type</a>
    <br>
    <a href="#step-2-4" style="text-decoration: none; color: #006769"><span style="font-size: 24px; color: rgb(0, 65, 75)">&#10125;</span> Spreads the "t+h" values over the remaining decimal values </a>
    <br>
    <a href="#step-2-5" style="text-decoration: none; color: #006769"><span style="font-size: 24px; color: rgb(0, 65, 75)">&#10126;</span> Exporting to excel file </a>
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
   <span>Set key variables to fill the growth_rates with 't+h' values</span>
  </div>

In [9]:
# Call the function to show the h_initial window
h_initial = show_h_initial_window()
print("Selected h_initial:", h_initial)

Selected h_initial: 3


In [10]:
# Call the function to show the start_row window
start_row = show_start_row_window()
print("Selected start_row:", start_row)

Selected start_row: 0


In [11]:
# Define the mapping of frequencies to h_counter values
frequency_mapping = {
    'monthly': 1,
    'quarterly': 3,
    'annual': 12
}

# Get the appropriate h_counter value based on the selected frequency
h_counter = frequency_mapping.get(frequency)
print("Selected h_counter:", h_counter)

Selected h_counter: 1


<div id="step-2-1">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10122;</span> <span>Replace decimal values by “t+h” values only in the rows representing a new rung</span>
  </div>

In [12]:
horizon = replace_horizon(growth_rates_df.iloc[:, 3:], start_row, h_initial, h_counter)
horizon_df = horizon.copy()
horizon_df.head(10)

sep_2011 oct_2011 nov_2011 dic_2011 ene_2012 feb_2012 mar_2012 abr_2012  \
0     t+15     t+14     t+13     t+12     t+11     t+10      t+9      t+8   
1      5.9      5.3      5.1      6.0      5.5      6.9      5.7      4.5   
2      NaN      NaN     t+13     t+12     t+11     t+10      t+9      t+8   
3      NaN      NaN      5.1      6.0      5.5      6.9      5.7      4.5   
4      NaN      NaN      5.1      6.0      5.5      6.9      5.7      4.5   
5      NaN      NaN      5.1      6.0      5.5      6.9      5.7      4.5   
6      NaN      NaN      5.1      6.0      5.5      6.9      5.7      4.5   
7      NaN      NaN      NaN     t+13     t+12     t+11     t+10      t+9   
8      NaN      NaN      NaN      6.0      5.5      6.9      5.7      4.6   
9      NaN      NaN      NaN      6.0      5.5      6.9      5.7      4.6   

  may_2012 jun_2012 jul_2012 ago_2012 sep_2012 oct_2012 nov_2012 dic_2012  \
0      t+7      t+6      t+5      t+4      t+3      NaN      NaN      NaN   
1      7.0      7.3      7.4      6.3      5.9      NaN      NaN      NaN   
2      t+7      t+6      t+5      t+4      t+3      t+2      t+1      NaN   
3      7.0      7.3      7.4      6.3      5.9      6.7      6.8      NaN   
4      7.0      7.3      7.4      6.3      5.9      6.7      6.8      NaN   
5      7.0      7.3      7.4      6.3      5.9      6.7      6.8      NaN   
6      7.0      7.3      7.4      6.3      5.9      6.7      6.8      NaN   
7      t+8      t+7      t+6      t+5      t+4      t+3      t+2      t+1   
8      7.1      7.4      7.5      6.5      6.3      6.8      6.8      4.3   
9      7.1      7.4      7.5      6.5      6.3      6.8      6.8      4.3   

  ene_2013 feb_2013 mar_2013 abr_2013 may_2013 jun_2013 jul_2013 ago_2013  \
0      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
1      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
2      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
3      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
4      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
5      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
6      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
7      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
8      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
9      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   

  sep_2013 oct_2013 nov_2013 dic_2013 ene_2014 feb_2014 mar_2014 abr_2014  \
0      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
1      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
2      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
3      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
4      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
5      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
6      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
7      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
8      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
9      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   

  may_2014 jun_2014 jul_2014 ago_2014 sep_2014 oct_2014 nov_2014 dic_2014  \
0      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
1      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
2      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
3      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
4      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
5      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
6      NaN      NaN      NaN      NaN      NaN      NaN      NaN      N

<div id="step-2-2">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10123;</span> <span>Concatenate first 3 columns: year, date, id_ns</span>
  </div>

In [13]:
# Get the first three columns of the original DataFrame
first_3_columns = growth_rates_df.iloc[:, :3]

# Concatenate the first three columns with h_{sector}_{frequency}_growth_rates
horizon_df = pd.concat([first_3_columns, horizon_df], axis=1)
horizon_df.head(20)

year id_ns       date sep_2011 oct_2011 nov_2011 dic_2011 ene_2012  \
0   2013    01 2013-01-04     t+15     t+14     t+13     t+12     t+11   
1   2013    02 2013-01-11      5.9      5.3      5.1      6.0      5.5   
2   2013    03 2013-01-18      NaN      NaN     t+13     t+12     t+11   
3   2013    04 2013-01-25      NaN      NaN      5.1      6.0      5.5   
4   2013    05 2013-02-01      NaN      NaN      5.1      6.0      5.5   
5   2013    06 2013-02-08      NaN      NaN      5.1      6.0      5.5   
6   2013    07 2013-02-15      NaN      NaN      5.1      6.0      5.5   
7   2013    08 2013-02-22      NaN      NaN      NaN     t+13     t+12   
8   2013    09 2013-03-01      NaN      NaN      NaN      6.0      5.5   
9   2013    10 2013-03-08      NaN      NaN      NaN      6.0      5.5   
10  2013    11 2013-03-15      NaN      NaN      NaN      6.0      5.5   
11  2013    12 2013-03-22      NaN      NaN      NaN      NaN     t+13   
12  2013    13 2013-04-05      NaN      NaN      NaN      NaN      5.5   
13  2013    14 2013-04-12      NaN      NaN      NaN      NaN      5.5   
14  2013    15 2013-04-19      NaN      NaN      NaN      NaN      NaN   
15  2013    16 2013-04-26      NaN      NaN      NaN      NaN      NaN   
16  2013    17 2013-05-03      NaN      NaN      NaN      NaN      NaN   
17  2013    18 2013-05-10      NaN      NaN      NaN      NaN      NaN   
18  2013    19 2013-05-17      NaN      NaN      NaN      NaN      NaN   
19  2013    20 2013-05-24      NaN      NaN      NaN      NaN      NaN   
20  2013    21 2013-05-31      NaN      NaN      NaN      NaN      NaN   
21  2013    22 2013-06-07      NaN      NaN      NaN      NaN      NaN   
22  2013    23 2013-06-14      NaN      NaN      NaN      NaN      NaN   
23  2013    24 2013-06-21      NaN      NaN      NaN      NaN      NaN   
24  2013    25 2013-06-27      NaN      NaN      NaN      NaN      NaN   
25  2013    26 2013-07-05      NaN      NaN      NaN      NaN      NaN   
26  2013    27 2013-07-12      NaN      NaN      NaN      NaN      NaN   
27  2013    28 2013-07-19      NaN      NaN      NaN      NaN      NaN   
28  2013    29 2013-07-26      NaN      NaN      NaN      NaN      NaN   
29  2013    30 2013-08-09      NaN      NaN      NaN      NaN      NaN   
30  2013    31 2013-08-16      NaN      NaN      NaN      NaN      NaN   
31  2013    32 2013-08-23      NaN      NaN      NaN      NaN      NaN   
32  2013    33 2013-08-29      NaN      NaN      NaN      NaN      NaN   
33  2013    34 2013-09-06      NaN      NaN      NaN      NaN      NaN   
34  2013    35 2013-09-13      NaN      NaN      NaN      NaN      NaN   
35  2013    36 2013-09-20      NaN      NaN      NaN      NaN      NaN   
36  2013    37 2013-09-27      NaN      NaN      NaN      NaN      NaN   
37  2013    38 2013-10-04      NaN      NaN      NaN      NaN      NaN   
38  2013    39 2013-10-11      NaN      NaN      NaN      NaN      NaN   
39  2013    40 2013-10-18      NaN      NaN      NaN      NaN      NaN   
40  2013    41 2013-10-25      NaN      NaN      NaN      NaN      NaN   
41  2013    42 2013-10-31      NaN      NaN      NaN      NaN      NaN   
42  2013    43 2013-11-08      NaN      NaN      NaN      NaN      NaN   
43  2013    44 2013-11-15      NaN      NaN      NaN      NaN      NaN   
44  2013    45 2013-11-22      NaN      NaN      NaN      NaN      NaN   
45  2013    46 2013-11-29      NaN      NaN      NaN      NaN      NaN   
46  2013    47 2013-12-06      NaN      NaN      NaN      NaN      NaN   
47  2013    48 2013-12-13      NaN      NaN      NaN      NaN      NaN   
48  2013    49 2013-12-20      NaN      NaN      NaN      NaN      NaN   
49  2013    50 2013-12-27      NaN      NaN      NaN      NaN      NaN   
50  2014    01 2014-01-10      NaN      NaN      NaN      NaN      NaN   
51  2014    02 2014-01-17      NaN      NaN      NaN      NaN      NaN   
52  2014    03 2014-01-24      NaN      NaN      NaN      NaN      NaN   
53  2014

<div id="step-2-3">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10124;</span> <span>Convert columns to string type</span>
  </div>

In [14]:
horizon_df = columns_str(horizon_df)
horizon_df.head(20)

year id_ns       date sep_2011 oct_2011 nov_2011 dic_2011 ene_2012  \
0   2013    01 2013-01-04     t+15     t+14     t+13     t+12     t+11   
1   2013    02 2013-01-11      5.9      5.3      5.1      6.0      5.5   
2   2013    03 2013-01-18                       t+13     t+12     t+11   
3   2013    04 2013-01-25                        5.1      6.0      5.5   
4   2013    05 2013-02-01                        5.1      6.0      5.5   
5   2013    06 2013-02-08                        5.1      6.0      5.5   
6   2013    07 2013-02-15                        5.1      6.0      5.5   
7   2013    08 2013-02-22                                t+13     t+12   
8   2013    09 2013-03-01                                 6.0      5.5   
9   2013    10 2013-03-08                                 6.0      5.5   
10  2013    11 2013-03-15                                 6.0      5.5   
11  2013    12 2013-03-22                                         t+13   
12  2013    13 2013-04-05                                          5.5   
13  2013    14 2013-04-12                                          5.5   
14  2013    15 2013-04-19                                                
15  2013    16 2013-04-26                                                
16  2013    17 2013-05-03                                                
17  2013    18 2013-05-10                                                
18  2013    19 2013-05-17                                                
19  2013    20 2013-05-24                                                
20  2013    21 2013-05-31                                                
21  2013    22 2013-06-07                                                
22  2013    23 2013-06-14                                                
23  2013    24 2013-06-21                                                
24  2013    25 2013-06-27                                                
25  2013    26 2013-07-05                                                
26  2013    27 2013-07-12                                                
27  2013    28 2013-07-19                                                
28  2013    29 2013-07-26                                                
29  2013    30 2013-08-09                                                
30  2013    31 2013-08-16                                                
31  2013    32 2013-08-23                                                
32  2013    33 2013-08-29                                                
33  2013    34 2013-09-06                                                
34  2013    35 2013-09-13                                                
35  2013    36 2013-09-20                                                
36  2013    37 2013-09-27                                                
37  2013    38 2013-10-04                                                
38  2013    39 2013-10-11                                                
39  2013    40 2013-10-18                                                
40  2013    41 2013-10-25                                                
41  2013    42 2013-10-31                                                
42  2013    43 2013-11-08                                                
43  2013    44 2013-11-15                                                
44  2013    45 2013-11-22                                                
45  2013    46 2013-11-29                                                
46  2013    47 2013-12-06                                                
47  2013    48 2013-12-13                                                
48  2013    49 2013-12-20                                                
49  2013    50 2013-12-27                                                
50  2014    01 2014-01-10                                                
51  2014    02 2014-01-17                                                
52  2014    03 2014-01-24                                                
53  2014

<div id="step-2-4">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10125;</span> Spreads the "t+h" values over the remaining decimal values
  </div>

In [16]:
horizon_df = replace_horizon_1(horizon_df)
horizon_df.head(20)

year id_ns       date sep_2011 oct_2011 nov_2011 dic_2011 ene_2012  \
0   2013    01 2013-01-04     t+15     t+14     t+13     t+12     t+11   
1   2013    02 2013-01-11     t+15     t+14     t+13     t+12     t+11   
2   2013    03 2013-01-18                       t+13     t+12     t+11   
3   2013    04 2013-01-25                       t+13     t+12     t+11   
4   2013    05 2013-02-01                       t+14     t+13     t+12   
5   2013    06 2013-02-08                       t+14     t+13     t+12   
6   2013    07 2013-02-15                       t+14     t+13     t+12   
7   2013    08 2013-02-22                                t+13     t+12   
8   2013    09 2013-03-01                                t+14     t+13   
9   2013    10 2013-03-08                                t+14     t+13   
10  2013    11 2013-03-15                                t+14     t+13   
11  2013    12 2013-03-22                                         t+13   
12  2013    13 2013-04-05                                         t+14   
13  2013    14 2013-04-12                                         t+14   
14  2013    15 2013-04-19                                                
15  2013    16 2013-04-26                                                
16  2013    17 2013-05-03                                                
17  2013    18 2013-05-10                                                
18  2013    19 2013-05-17                                                
19  2013    20 2013-05-24                                                

   feb_2012 mar_2012 abr_2012 may_2012 jun_2012 jul_2012 ago_2012 sep_2012  \
0      t+10      t+9      t+8      t+7      t+6      t+5      t+4      t+3   
1      t+10      t+9      t+8      t+7      t+6      t+5      t+4      t+3   
2      t+10      t+9      t+8      t+7      t+6      t+5      t+4      t+3   
3      t+10      t+9      t+8      t+7      t+6      t+5      t+4      t+3   
4      t+11     t+10      t+9      t+8      t+7      t+6      t+5      t+4   
5      t+11     t+10      t+9      t+8      t+7      t+6      t+5      t+4   
6      t+11     t+10      t+9      t+8      t+7      t+6      t+5      t+4   
7      t+11     t+10      t+9      t+8      t+7      t+6      t+5      t+4   
8      t+12     t+11     t+10      t+9      t+8      t+7      t+6      t+5   
9      t+12     t+11     t+10      t+9      t+8      t+7      t+6      t+5   
10     t+12     t+11     t+10      t+9      t+8      t+7      t+6      t+5   
11     t+12     t+11     t+10      t+9      t+8      t+7      t+6      t+5   
12     t+13     t+12     t+11     t+10      t+9      t+8      t+7      t+6   
13     t+13     t+12     t+11     t+10      t+9      t+8      t+7      t+6   
14     t+13     t+12     t+11     t+10      t+9      t+8      t+7      t+6   
15     t+13     t+12     t+11     t+10      t+9      t+8      t+7      t+6   
16     t+14     t+13     t+12     t+11     t+10      t+9      t+8      t+7   
17     t+14     t+13     t+12     t+11     t+10      t+9      t+8      t+7   
18     t+14     t+13     t+12     t+11     t+10      t+9      t+8      t+7   
19              t+13     t+12     t+11     t+10      t+9      t+8      t+7   

   oct_2012 nov_2012 dic_2012 ene_2013 feb_2013 mar_2013 abr_2013 may_2013  \
0                                                                            
1                                                                            
2       t+2      t+1                                                         
3       t+2      t+1                                                         
4       t+3      t+2                                                         
5       t+3      t+2                                                         
6       t+3      t+2                                                         
7       t+3      t+2      t+1                                                
8       t+4      t+3      t+2                                                
9       t+4      t+3      t+2 

<div id="step-2-5">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10126;</span> Exporting to excel file
  </div>

In [ ]:
#def export_to_excel(df, filename):
#    # Exportar el DataFrame como un archivo Excel
#    df.to_excel(filename, index=False)

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 20px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#steps-2" style="color: #006769; text-decoration: none;">⮝</a>
    </span> 
    <a href="#steps-2" style="color: #006769; text-decoration: none;">Back to steps.</a>
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">Back to the outline.</a>
</div>

<div id="3">
   <!-- Contenido de la celda de destino -->
</div>

<h1><span style = "color: rgb(0, 65, 75); font-family: PT Serif Pro Book;">3.</span> <span style = "color: dark; font-family: PT Serif Pro Book;">Create growth rates by horizon dataset</span></h1>

<div id="steps-3">
   <!-- Contenido de la celda de destino -->
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <a href="#st-3-1" style="text-decoration: none; color: #006769"> <span style="font-size: 24px; color: rgb(0, 65, 75);">&#10122;</span> Generating a dictionary with the row indices and their t+h values</a>
    <br>
    <a href="#st-3-2" style="text-decoration: none; color: #006769"><span style="font-size: 24px; color: rgb(0, 65, 75)">&#10123;</span> Colapse growth rates by horizon ('t+h') </a>
    <br>
</div>

<div id="st-3-1">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10122;</span> <span>Generating a dictionary with the row indices and their t+h values</span>
  </div>

In [17]:
dictionary = get_last_index_h(horizon_df)

<div id="st-3-2">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10123;</span> <span>Colapse growth rates by horizon ('t+h')  </span>
  </div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; color: dark; font-size:16px">
    Note that <code>'t'</code> is the date of the first announcement, while <code>'t+h'</code> is 'h' months after the first announcement.
    <div/>

In [18]:
filtered_h_df = filter_df_by_indices(growth_rates_df, dictionary)
filtered_h_df

horizon  sep_2011  oct_2011  nov_2011  dic_2011  ene_2012  feb_2012  \
0        t       5.9       5.3       5.1       6.0       5.5       6.9   
1      t+1       NaN       NaN       5.1       6.0       5.5       6.9   
2      t+2       NaN       NaN       NaN       6.0       5.5       6.9   
3      t+3       NaN       NaN       NaN       NaN       5.5       6.9   
4      t+4       NaN       NaN       NaN       NaN       NaN       6.9   
5      t+5       NaN       NaN       NaN       NaN       NaN       NaN   
6      t+6       NaN       NaN       NaN       NaN       NaN       NaN   
7      t+7       NaN       NaN       NaN       NaN       NaN       NaN   
8      t+8       NaN       NaN       NaN       NaN       NaN       NaN   
9      t+9       NaN       NaN       NaN       NaN       NaN       NaN   
10    t+10       NaN       NaN       NaN       NaN       NaN       NaN   
11    t+11       NaN       NaN       NaN       NaN       NaN       NaN   
12    t+12       NaN       NaN       NaN       NaN       NaN       NaN   
13    t+13       NaN       NaN       NaN       NaN       NaN       NaN   
14    t+14       NaN       NaN       NaN       NaN       NaN       NaN   
15    t+15       NaN       NaN       NaN       NaN       NaN       NaN   

    mar_2012  abr_2012  may_2012  jun_2012  jul_2012  ago_2012  sep_2012  \
0        5.7       4.5       7.0       7.3       7.4       6.3       5.9   
1        5.7       4.6       7.1       7.4       7.5       6.5       6.3   
2        5.7       4.6       7.1       7.4       7.5       6.5       6.3   
3        5.7       4.6       7.1       7.4       7.5       6.5       6.3   
4        5.7       4.6       7.1       7.4       7.5       6.5       6.3   
5        5.7       4.6       7.1       7.4       7.5       6.5       6.3   
6        NaN       4.6       7.1       7.4       7.5       6.5       6.3   
7        NaN       NaN       7.1       7.3       7.6       6.6       6.0   
8        NaN       NaN       NaN       7.3       7.6       6.6       6.0   
9        NaN       NaN       NaN       NaN       7.6       6.6       6.0   
10       NaN       NaN       NaN       NaN       NaN       6.6       6.3   
11       NaN       NaN       NaN       NaN       NaN       NaN       6.3   
12       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
13       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
14       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
15       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

    oct_2012  nov_2012  dic_2012  ene_2013  feb_2013  mar_2013  abr_2013  \
0        6.7       6.8       4.3       6.2       5.0       3.0       7.7   
1        6.8       6.8       4.3       6.2       5.1       3.0       7.7   
2        6.8       6.8       4.3       6.4       5.1       3.0       7.6   
3        6.8       6.8       4.3       6.4       5.1       2.4       7.6   
4        6.8       6.8       4.3       6.4       4.9       2.4       7.6   
5        6.8       6.8       4.3       6.4       4.9       2.4       7.7   
6        6.8       6.8       4.4       6.4       4.9       2.5       7.7   
7        6.9       6.6       4.4       6.4       5.0       2.5       7.7   
8        6.9       6.6       4.4       6.4       5.0       2.5       7.8   
9        6.9       6.6       4.3       6.4       4.9       2.5       8.5   
10       6.8       6.8       4.3       6.4       5.1       2.7       8.5   
11       6.8       6.8       4.3       6.7       4.2       2.7       8.8   
12       6.8       6.8       4.3       6.1       4.2       2.9       8.8   
13       NaN       6.8       4.3       6.1       4.2       2.9       8.8   
14       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
15       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

    may_2013  jun_2013  jul_2013  ago_2013  sep_2013  oct_2013  nov_2013  \
0        5.0       4.4       4.5       4.3       4.4       5.4       4.8   
1     

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 20px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#steps-1" style="color: #006769; text-decoration: none;">⮝</a>
    </span> 
    <a href="#steps-3" style="color: #006769; text-decoration: none;">Back to steps.</a>
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">Back to the outline.</a>
</div>

<div id="4">
   <!-- Contenido de la celda de destino -->
</div>

<h1><span style = "color: rgb(0, 65, 75); font-family: PT Serif Pro Book;">4.</span> <span style = "color: dark; font-family: PT Serif Pro Book;">Create vintages and releases datasets</span></h1>

<div id="steps-4">
   <!-- Contenido de la celda de destino -->
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <a href="#st-4-1" style="text-decoration: none; color: #006769"> <span style="font-size: 24px; color: rgb(0, 65, 75);">&#10122;</span> Create vintages</a>
    <br>
    <a href="#st-4-2" style="text-decoration: none; color: #006769"><span style="font-size: 24px; color: rgb(0, 65, 75)">&#10123;</span> Clean-up vintages dataframe </a>
    <br>
    <a href="#st-4-3" style="text-decoration: none; color: #006769"><span style="font-size: 24px; color: rgb(0, 65, 75)">&#10124;</span> Create releases </a>
    <br>
</div>

<div id="st-4-1">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10122;</span> <span>Create vintages</span>
  </div>

In [19]:
vintages = create_vintages(growth_rates)
vintages

aux vintages_date  ns_2013m01  ns_2013m02  ns_2013m03  ns_2013m04  ns_2013m05  \
0        sep_2011         NaN         NaN         NaN         NaN         NaN   
1        oct_2011         NaN         NaN         NaN         NaN         NaN   
2        nov_2011         5.1         NaN         NaN         NaN         NaN   
3        dic_2011         6.0         6.0         NaN         NaN         NaN   
4        ene_2012         5.5         5.5         5.5         NaN         NaN   
5        feb_2012         6.9         6.9         6.9         6.9         NaN   
6        mar_2012         5.7         5.7         5.7         5.7         5.7   
7        abr_2012         4.5         4.6         4.6         4.6         4.6   
8        may_2012         7.0         7.1         7.1         7.1         7.1   
9        jun_2012         7.3         7.4         7.4         7.4         7.4   
10       jul_2012         7.4         7.5         7.5         7.5         7.5   
11       ago_2012         6.3         6.5         6.5         6.5         6.5   
12       sep_2012         5.9         6.3         6.3         6.3         6.3   
13       oct_2012         6.7         6.8         6.8         6.8         6.8   
14       nov_2012         6.8         6.8         6.8         6.8         6.8   
15       dic_2012         NaN         4.3         4.3         4.3         4.3   
16       ene_2013         NaN         NaN         6.2         6.2         6.4   
17       feb_2013         NaN         NaN         NaN         5.0         5.1   
18       mar_2013         NaN         NaN         NaN         NaN         3.0   
19       abr_2013         NaN         NaN         NaN         NaN         NaN   
20       may_2013         NaN         NaN         NaN         NaN         NaN   
21       jun_2013         NaN         NaN         NaN         NaN         NaN   
22       jul_2013         NaN         NaN         NaN         NaN         NaN   
23       ago_2013         NaN         NaN         NaN         NaN         NaN   
24       sep_2013         NaN         NaN         NaN         NaN         NaN   
25       oct_2013         NaN         NaN         NaN         NaN         NaN   
26       nov_2013         NaN         NaN         NaN         NaN         NaN   
27       dic_2013         NaN         NaN         NaN         NaN         NaN   
28       ene_2014         NaN         NaN         NaN         NaN         NaN   
29       feb_2014         NaN         NaN         NaN         NaN         NaN   
30       mar_2014         NaN         NaN         NaN         NaN         NaN   
31       abr_2014         NaN         NaN         NaN         NaN         NaN   
32       may_2014         NaN         NaN         NaN         NaN         NaN   
33       jun_2014         NaN         NaN         NaN         NaN         NaN   
34       jul_2014         NaN         NaN         NaN         NaN         NaN   
35       ago_2014         NaN         NaN         NaN         NaN         NaN   
36       sep_2014         NaN         NaN         NaN         NaN         NaN   
37       oct_2014         NaN         NaN         NaN         NaN         NaN   
38       nov_2014         NaN         NaN         NaN         NaN         NaN   
39       dic_2014         NaN         NaN         NaN         NaN         NaN   
40       ene_2015         NaN         NaN         NaN         NaN         NaN   
41       feb_2015         NaN         NaN         NaN         NaN         NaN   
42       mar_2015         NaN         NaN         NaN         NaN         NaN   
43       abr_2015         NaN         NaN         NaN         NaN         NaN   
44       may_2015         NaN         NaN         NaN         NaN         NaN   
45       jun_2015         NaN         NaN         NaN         NaN         NaN   
46       jul_2015         NaN         NaN         NaN         NaN         NaN   
47       ago_2015         NaN         NaN         NaN         NaN         NaN   
48       sep_2015         NaN  

<div id="st-4-2">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10123;</span> <span>Clean-up vintages dataframe</span>
  </div>

In [20]:
# Call the appropriate function
if frequency == 'monthly':
    vintages_df = process_monthly(vintages)
elif frequency == 'quarterly':
    vintages_df = process_quarterly(vintages)
elif frequency == 'annual':
    vintages_df = process_annual(vintages)

# Display the result
vintages_df

aux vintages_date  ns_2013m01  ns_2013m02  ns_2013m03  ns_2013m04  ns_2013m05  \
0      2011-09-01         NaN         NaN         NaN         NaN         NaN   
1      2011-10-01         NaN         NaN         NaN         NaN         NaN   
2      2011-11-01         5.1         NaN         NaN         NaN         NaN   
3      2011-12-01         6.0         6.0         NaN         NaN         NaN   
4      2012-01-01         5.5         5.5         5.5         NaN         NaN   
5      2012-02-01         6.9         6.9         6.9         6.9         NaN   
6      2012-03-01         5.7         5.7         5.7         5.7         5.7   
7      2012-04-01         4.5         4.6         4.6         4.6         4.6   
8      2012-05-01         7.0         7.1         7.1         7.1         7.1   
9      2012-06-01         7.3         7.4         7.4         7.4         7.4   
10     2012-07-01         7.4         7.5         7.5         7.5         7.5   
11     2012-08-01         6.3         6.5         6.5         6.5         6.5   
12     2012-09-01         5.9         6.3         6.3         6.3         6.3   
13     2012-10-01         6.7         6.8         6.8         6.8         6.8   
14     2012-11-01         6.8         6.8         6.8         6.8         6.8   
15     2012-12-01         NaN         4.3         4.3         4.3         4.3   
16     2013-01-01         NaN         NaN         6.2         6.2         6.4   
17     2013-02-01         NaN         NaN         NaN         5.0         5.1   
18     2013-03-01         NaN         NaN         NaN         NaN         3.0   
19     2013-04-01         NaN         NaN         NaN         NaN         NaN   
20     2013-05-01         NaN         NaN         NaN         NaN         NaN   
21     2013-06-01         NaN         NaN         NaN         NaN         NaN   
22     2013-07-01         NaN         NaN         NaN         NaN         NaN   
23     2013-08-01         NaN         NaN         NaN         NaN         NaN   
24     2013-09-01         NaN         NaN         NaN         NaN         NaN   
25     2013-10-01         NaN         NaN         NaN         NaN         NaN   
26     2013-11-01         NaN         NaN         NaN         NaN         NaN   
27     2013-12-01         NaN         NaN         NaN         NaN         NaN   
28     2014-01-01         NaN         NaN         NaN         NaN         NaN   
29     2014-02-01         NaN         NaN         NaN         NaN         NaN   
30     2014-03-01         NaN         NaN         NaN         NaN         NaN   
31     2014-04-01         NaN         NaN         NaN         NaN         NaN   
32     2014-05-01         NaN         NaN         NaN         NaN         NaN   
33     2014-06-01         NaN         NaN         NaN         NaN         NaN   
34     2014-07-01         NaN         NaN         NaN         NaN         NaN   
35     2014-08-01         NaN         NaN         NaN         NaN         NaN   
36     2014-09-01         NaN         NaN         NaN         NaN         NaN   
37     2014-10-01         NaN         NaN         NaN         NaN         NaN   
38     2014-11-01         NaN         NaN         NaN         NaN         NaN   
39     2014-12-01         NaN         NaN         NaN         NaN         NaN   
40     2015-01-01         NaN         NaN         NaN         NaN         NaN   
41     2015-02-01         NaN         NaN         NaN         NaN         NaN   
42     2015-03-01         NaN         NaN         NaN         NaN         NaN   
43     2015-04-01         NaN         NaN         NaN         NaN         NaN   
44     2015-05-01         NaN         NaN         NaN         NaN         NaN   
45     2015-06-01         NaN         NaN         NaN         NaN         NaN   
46     2015-07-01         NaN         NaN         NaN         NaN         NaN   
47     2015-08-01         NaN         NaN         NaN         NaN         NaN   
48     2015-09-01         NaN  

<div id="st-4-3">
   <!-- Contenido de la celda de destino -->
</div>

<div style="text-align: left; font-family: 'PT Serif Pro Book'; font-size:22px">
    <span style="font-size: 24px; color: rgb(0, 65, 75)">&#10124;</span> <span>Create releases</span>
  </div>

In [21]:
releases_df = create_releases(vintages_df, sector)
releases_df

aux vintages_date  gdp_release_1  gdp_release_2  gdp_release_3  gdp_release_4  \
0      2011-09-01            NaN            NaN            NaN            NaN   
1      2011-10-01            NaN            NaN            NaN            NaN   
2      2011-11-01            5.1            NaN            NaN            NaN   
3      2011-12-01            6.0            6.0            NaN            NaN   
4      2012-01-01            5.5            5.5            5.5            NaN   
5      2012-02-01            6.9            6.9            6.9            6.9   
6      2012-03-01            5.7            5.7            5.7            5.7   
7      2012-04-01            4.5            4.6            4.6            4.6   
8      2012-05-01            7.0            7.1            7.1            7.1   
9      2012-06-01            7.3            7.4            7.4            7.4   
10     2012-07-01            7.4            7.5            7.5            7.5   
11     2012-08-01            6.3            6.5            6.5            6.5   
12     2012-09-01            5.9            6.3            6.3            6.3   
13     2012-10-01            6.7            6.8            6.8            6.8   
14     2012-11-01            6.8            6.8            6.8            6.8   
15     2012-12-01            4.3            4.3            4.3            4.3   
16     2013-01-01            6.2            6.2            6.4            6.4   
17     2013-02-01            5.0            5.1            5.1            5.1   
18     2013-03-01            3.0            3.0            3.0            2.4   
19     2013-04-01            7.7            7.7            7.6            7.6   
20     2013-05-01            5.0            4.8            4.8            4.8   
21     2013-06-01            4.4            4.4            4.4            4.4   
22     2013-07-01            4.5            4.5            4.6            4.6   
23     2013-08-01            4.3            4.3            4.3            4.3   
24     2013-09-01            4.4            4.4            4.4            4.4   
25     2013-10-01            5.4            5.4            5.5            6.1   
26     2013-11-01            4.8            5.0            7.2            7.2   
27     2013-12-01            5.0            6.7            6.7            6.9   
28     2014-01-01            4.2            4.2            4.0            4.0   
29     2014-02-01            5.7            5.4            5.4            5.4   
30     2014-03-01            4.9            4.9            4.9            5.4   
31     2014-04-01            2.0            2.0            2.4            2.4   
32     2014-05-01            1.8            2.3            2.3            2.3   
33     2014-06-01            0.3            0.3            0.3            0.3   
34     2014-07-01            1.2            1.2            1.3            1.3   
35     2014-08-01            1.2            1.3            1.3            1.3   
36     2014-09-01            2.7            2.7            2.7            2.7   
37     2014-10-01            2.4            2.4            2.4            2.4   
38     2014-11-01            0.3            0.2            0.2            0.2   
39     2014-12-01            0.5            0.5            0.5            0.5   
40     2015-01-01            1.7            1.7            1.5            1.5   
41     2015-02-01            0.9            1.0            1.0            1.0   
42     2015-03-01            2.7            2.7            2.7            2.7   
43     2015-04-01            4.3            4.3            4.2            4.2   
44     2015-05-01            1.2            1.1            1.1            1.1   
45     2015-06-01            3.9            3.9            3.9            3.9   
46     2015-07-01            3.3            3.3            3.3            3.3   
47     2015-08-01            2.6            2.6            2.6            2.4   
48     2015-09-01            3.

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 20px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#steps-4" style="color: #006769; text-decoration: none;">⮝</a>
    </span> 
    <a href="#steps-4" style="color: #006769; text-decoration: none;">Back to steps.</a>
</div>

#### Check column type

In [22]:
print(releases_df['gdp_release_1'].dtype)

float64


In [23]:
print(releases_df['gdp_release_1'].dtype)

float64


<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">Back to the outline.</a>
</div>

<div id="5">
   <!-- Contenido de la celda de destino -->
</div>

<h2><span style = "color: rgb(0, 65, 75); font-family: charter;">5.</span>
    <span style = "color: dark; font-family: charter;">
    Loading to SQL
    </span>
    </h2>

In [ ]:
# Check if all environment variables are defined
if not all([host, user, password]):
    raise ValueError("Some environment variables are missing (CIUP_SQL_HOST, CIUP_SQL_USER, CIUP_SQL_PASS)")

# Create connection string
connection_string = f"postgresql://{user}:{password}@{host}:{port}/{database}"

# Create SQLAlchemy engine
engine = create_engine(connection_string)

# REVISIONES

#horizon_df.to_sql(f'{sector}_{frequency}_growth_rates_horizon', engine, index=False, if_exists='replace')
#filtered_h_df.to_sql(f'{sector}_{frequency}_h', engine, index=False, if_exists='replace')
#vintages_df.to_sql(f'{sector}_{frequency}_vintages', engine, index=False, if_exists='replace')
#releases_df.to_sql(f'{sector}_{frequency}_releases', engine, index=False, if_exists='replace')

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 20px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#step-1-1" style="color: rgb(255, 32, 78); text-decoration: none;">⮝</a>
    </span> 
    <a href="#step-1-1" style="color: rgb(255, 32, 78); text-decoration: none;">Back to <b>select economic sector</b>.</a>
</div>

<div style="font-family: PT Serif Pro Book; text-align: left; color: dark; font-size: 16px;">
    <span style="font-size: 30px; color: rgb(255, 32, 78); font-weight: bold;">
        <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">&#11180;</a>
    </span> 
    <a href="#outilne" style="color: rgb(0, 153, 123); text-decoration: none;">Back to the outline.</a>
</div>